#CS 145 Project3

## Predicting the Development Level of a Country/Region with Educational Statistics

- Authors: Ziqi Wang (wangziqi) ; Hang Jiang (hjian42)
- Please check the link if you want to see an image: https://colab.research.google.com/drive/1f5J_vMx1xvr2EsiMZt-eJHpTk4qUtsAv

#Introduction and Project Setup
- In this project, we use the dataset called `world_bank_intl_education`.
- This dataset records each country's `GDP per Captia` annually from 1970 to 2016.  242 countries / areas are included in the dataset.This dataset also records each country's educational status periodically. Therefore, we wonder whether it is possible to predict the GDP level of a country at a certain year using those educational statistics. More specifically, we want to formalize the problem into a **binary classification task: to predict the economic development level of a country  in a certain year by** using its educational features such as education equality, tertiary school, etc. In total, there are 9196 GDP-per-captia tuples for distinct (country, year). 
- To evaluate the development  level of a country, we decide to categorize the economic development level into developed country and developing country, and **we define a country "developed" if it has GDP per capita over $12,000, otherwise, "developing"**. Hence, we choose use *binary logistic regression model* to predict whether a country is a developed one or not by giving the confidence
- The challenging part of the task is to locate, create, and analyze features related to (but not limited to) education from thousands of surveys in the dataset. We will show you how we analyze those features against `GDP per Captia` and pick the most important features for the classification task. Considering the fact that most countries' development level is comparatively stable from 1970 to 2016. We will not include any country name information as features. Otherwise, if a classifier learns USA is a "developed" country in 2000, it is almost cheating for the classifier to predict USA as "developed" for the following years if the classifier knows the country name of the instance. 
- Find your project_id: https://console.cloud.google.com/cloud-resource-manager, we build our client and import necessary libraries. 


In [0]:
# Run this cell to authenticate yourself to BigQuery.
from google.colab import auth
auth.authenticate_user()
project_id = "rapid-snowfall-218803"

In [0]:
# Initialize BiqQuery client
from google.cloud import bigquery
client = bigquery.Client(project=project_id)  # pass in your projectid

In [0]:
# Some imports you will need
import seaborn as sns
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import altair as alt
import pandas as pd
%matplotlib inline
plt.style.use('seaborn-whitegrid')

#1. Analysis of Dataset (10%)




##1.1 Overview and Schema Design

###1.1.1 Overview
  - Description: This dataset combines key education statistics from a variety of sources to provide a look at global literacy, spending, and access.
  - The dataset is around 600MB, and covers 9196 surveys conducted in 242 countries/areas. 

###1.1.2 E/R Diagram
  - ![ER Graph](https://drive.google.com/uc?export=view&id=12ceHOOBsdm-qogyoJ-vhu4Mfowv_xu3a)

###1.1.3 Explanatoin of the ER Diagram
- what your entities are? 
  - country: each country has diffrent properties (GDP, population) and is surveyed many times. 
  - series: series of surverys are conducted in many countries
- what the relationships between those entities are (including whether they are one-to-many, many-to-one, etc.)
  -  countries are `investigated by` series (surveys): many-to-many
- what your keys and foreign keys for your tables?
  - Table `country_summary` 
    - key: country_code
    - foreign key: No foreign key
  - Table `series_summary`
    - key: series_code
    - foreign key: no foreign key
  - Table: `international_education `
     - key: country_code + series_code + year
     - foreign key: country_code, series_code
   - Table: `country_series_definitions`
     - key: country_code + series_code
     - foreign key: country_code, series_code


###1.1.4 In terms of OKV, what is the property table out of the four tables?
The `international_education` dataset is the property table and is structured in OKV (actually with a small twist). It arranges the information as the format below:  
object | key | year | value  
where the object is country_code and the key is series_code.  
There are other fields which describe the keys and objects, but the overall structure is still OKV.   


###1.1.5 Schema Comprehension
- Property table: series_summary
- Object information: country_summary
- International_educatoin table key: (indicator_code, year)

##1.2 Briefly Estimating this Dataset
- What are the tradeoffs between the design of the dataset you chose as it is and other alternatives? And the reason the authors of the dataset chose this particular structure?

- To clearly demonstrate the dataset, it got some redundency. For example, the first table `country_series_definitions` shows the relaionship between the two entities country and series. While the table `international_education` are almost the same but adding attributes of the relationship year and value. 
- As for table `country_summary` and `series_summary`, they can further be decomposed bacause there are some FD's inside like {country_code}+ = {country_code, short_name, long_name, table_name}. The author tries to add all attributes in one table instead of creating more tables could make us read the table easier and understand what attributes a entities has easier. 
- The reason the author try to use this kind of structure is that it reduces the numbers of tables so we can easily find out entities and the relationship between them. 

#2. Exploring Dataset with Visualizations (60%)

##Explore 7 Topics to Extract Features

There are many educational and relevant features that are potentially helpful for us to predict the development level of a country/region at a year. We will explore 8 topics, and find features in each topics that we think that contribute to the classification task. 

Those are the 7 topics:
- Education Resource: e.g. proportion of population who are teachers
- Labor Population: e.g. labor is an outcome of education
- Government Policy: e.g. compulsory education 
- Employment: e.g. employment rate
- Learning Outcome: e.g. literacy rate
- Education Technology: e.g. computer use, internet use
- Attainment: how long and what percentage of students stay at school
- Education Index: an index to measure education level 

From each topic, we choose some features and find their correlations with GDP per Captia. We will choose the best features and use those to predict the development level of a country/area. 

Here are the **criteria** we follow to choose features:
1. whether the feature has strong correlation with GDP per Captia
2. whether we can extract the feature for enough years and countries. Since there are 9196 rows of (country, year, GDP per Captia) as labeled data, we will do `labeled_data LEFT JOIN feature_data` to keep the resulting table 9196 rows. Therefore, we want to avoid too many NULL values.
3. whether we have diverse features. we want to avoid using similar features and explore different features.

##2.1 Education Resource
- We try to figure out whether education resource reflects development level of a country. We hypothesize that **developed areas have more education resources**. For instance, education resource can be demonstrated by the pecentage of teachers in diferent levels. The percentage of teachers will be calculated by the percentage of the amount of teachers out of the over all population. 
- We locate a series of surveys about the teacher population in each age group:
  - K12 education
    - Teachers in pre-primary education, both sexes (number) ~5000
    - Teachers in primary education, both sexes (number) ~6000
    - Teachers in secondary general education, both sexes (number): too few ~1000
    - Teachers in secondary vocational education, both sexes (number): too few ~1000
    - Teachers in tertiary education programmes, both sexes (number)
We also have the whole population statistics for each country at every year. 
  - Population, total
- Therefore, we can calculate the proportion of teachers in each level using the series above. There are also teacher population surveys for female instead of both sexes, so we can calculate female-to-male ratio in some levels too.  




### 2.1.1 percentage of pre-primary and primary Teachers in the whole population
- Using `percentage of pre-primary and primary Teachers in the whole population` as x axi and `GDP per capita (current US$)` as y axi. 
- Observation: `percentage of pre-primary and primary Teachers in the whole population` and `GDP per Captia  (current US$)` have a strong positive correlation. Initially we want to also include the table about secondary education to calculate `percentage of K12  Teachers in the whole population`, however, secondary tables have many years missing and will cause 4/5 rows of the resulting table to have NULL values if we include it. Therefore, we only add pre-primary and primary statistics together and still achieve a great positive correlation. It confirms our hypothesis that developed areas tend to have more education resources (teachers). **Therefore, we decide to add it to our prediction model.**




In [0]:
%%bigquery --project $project_id q211
WITH combined_R AS (
    SELECT R1.country_name, R1.year, (R1.value+R2.value) combined_value
    FROM
    (SELECT country_name, value, year
    FROM `bigquery-public-data.world_bank_intl_education.international_education`
    WHERE indicator_name = "Teachers in pre-primary education, both sexes (number)") R1,
    (SELECT country_name, value, year
    FROM `bigquery-public-data.world_bank_intl_education.international_education`
    WHERE indicator_name = "Teachers in primary education, both sexes (number)") R2
    WHERE R1.country_name = R2.country_name AND R1.year = R2.year
)

SELECT c1.country_name, c1.value AS GDP, IF(c3.value!=0, c2.combined_value/c3.value, 0) percent, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` 
  WHERE indicator_name = "GDP per capita (current US$)" ) c1
  LEFT JOIN combined_R c2 ON c1.country_name = c2.country_name AND c1.year = c2.year
  LEFT JOIN
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education`
   WHERE indicator_name = "Population, total") c3
  ON c1.country_name = c3.country_name AND c1.year = c3.year

In [0]:
sampleq211 = q211.sample(5000)
alt.Chart(sampleq211).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("percent:Q", axis=alt.Axis(title="Percentage of pre-primary and primary teachers in population"))     
)

Chart({
  data:                                            country_name           GDP  \
  9034                             Bosnia and Herzegovina   1461.750520   
  8746                                 Sub-Saharan Africa    302.681409   
  7271                                         Bangladesh    199.336645   
  4825                                              Tonga    666.024775   
  6694                                           Maldives   9792.017334   
  8050                                       South Africa   2701.523815   
  4539                                              India    271.333596   
  752                                              Greece   3886.374253   
  3850                          Latin America & Caribbean   1842.250892   
  1613                                            Myanmar    643.951370   
  1596                                            Morocco    860.468326   
  6414                                            Vanuatu   2697.961375   
  4156  Middle East & North Africa (excluding high inc...   3156.328275   
  8551                                   Marshall Islands   2891.928956   
  1836                                           Cameroon   1215.808213   
  3178                                     Czech Republic  15183.636054   
  3437                                 Iran, Islamic Rep.    876.309241   
  6119                                            Lesotho    110.241719   
  7325                                         Low income    298.733476   
  8222                                      New Caledonia   4031.016039   
  994                                              Panama   2577.617944   
  3074                                      Middle income   3366.676622   
  4404                                              China    157.090374   
  2489                                         Costa Rica    766.088712   
  6522                                           Cameroon   1493.746567   
  63                                                 Iraq   3077.998472   
  6612                                           Honduras   1130.405046   
  1216                                            Belgium  10679.663892   
  4692                                              Samoa   1321.519135   
  3662                                Trinidad and Tobago  16530.180442   
  ...                                                 ...           ...   
  5486                                             Zambia   1104.587985   
  3474                                 Sub-Saharan Africa    583.329758   
  2760                                        High income  25768.958146   
  6539                                           Djibouti    768.176077   
  7845                                        Switzerland  88415.628061   
  1650                                            Senegal    756.608530   
  6746                                           Pakistan    332.475957   
  5306                                             Poland   4510.413117   
  8559                                   Marshall Islands   1604.248462   
  7715                                        New Zealand  11792.988694   
  5304                                             Poland  12421.318909   
  4792                                              Sudan    185.011170   
  4799                                              Tonga    724.370446   
  5896                                            Finland  23983.845754   
  239                                               Benin    322.777699   
  7495                                         Seychelles   4128.118232   
  2006                                           Mongolia   1717.898761   
  5872                                            Estonia   5308.347781   
  4205                                               Cuba    653.232915   
  1984                                           Maldives   2182.997011   
  3858                          Latin America & Caribbean   4310.148147   
  4915     

### 2.1.2 percentage of tertiary teachers in the whole population
- Using `percentage of tertiary teachers in the whole population` as x axi and `GDP per capita (current US$)` as y axi. 
- Observation: `percentage of tertiary teachers in the whole population` and `GDP per Captia  (current US$)` have a strong positive correlation. We calculate the percentage for tertiary education solely because it is different from K12 education and it has a different correlation with GDP (development level). 
It also confirms our hypothesis that developed areas tend to have more education resources (teachers). Since tertiary teacher population has a different distribution from primary teachers and has a strong correlation. **Therefore, we decide to add it to our prediction model.**

In [0]:
%%bigquery --project $project_id q212
SELECT c1.country_name, c1.value AS GDP, IF(c3.value!=0, c2.value/c3.value, 0) AS percent, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education`
   WHERE indicator_name = "Teachers in tertiary education programmes, both sexes (number)") c2
  ON c1.country_name = c2.country_name AND c1.year = c2.year
  LEFT JOIN 
   (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education`
    WHERE indicator_name = "Population, total") c3
  ON c1.country_name = c3.country_name AND c1.year = c3.year

In [150]:
sampleq212 = q212.sample(5000)
alt.Chart(sampleq212[sampleq212.percent < 0.012]).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("percent:Q", axis=alt.Axis(title="tertiary_teachers_population"),scale = alt.Scale(domain = [0.000,0.012]))     
)

Chart({
  data:                                      country_name           GDP   percent  \
  1087                                       Sweden  24080.899671  0.002874   
  3182                                 OECD members   8963.080276  0.002023   
  3512                               United Kingdom  46783.469217  0.002346   
  369                                         Japan  38096.211505  0.004286   
  2281                                    Australia  18249.288492  0.001630   
  2376                                    Indonesia    672.588111  0.000697   
  3031                                  New Zealand  17474.020315  0.002865   
  3874                          Lower middle income   2025.929064  0.000944   
  202                                         Aruba  20834.510199  0.001742   
  1315                                      Belgium  48424.575596  0.002485   
  91                                           Mali    322.538680  0.000090   
  3477                               European Union  12577.819599  0.001787   
  271                                         China    165.405540  0.000167   
  1160                                       Uganda    400.240950  0.000091   
  2997                                  Korea, Rep.   4686.137325  0.001365   
  1743                                      Romania   4676.315183  0.001447   
  3912                          Lower middle income    458.801630  0.000405   
  2874                                  El Salvador   3827.786267  0.001538   
  3633                             Macao SAR, China  17809.598155  0.002530   
  3514                               United Kingdom  39983.984675  0.001864   
  1136                                       Turkey   9036.266711  0.001409   
  1977                                     Colombia   1541.712369  0.001542   
  41                                           Cuba   1474.481630  0.000650   
  3257                                Cote d'Ivoire   1434.326615  0.000811   
  3291                                Middle income   1424.348200  0.000899   
  2415                                    Mauritius   1058.904835  0.000231   
  1520                                      Hungary  13029.883375  0.002369   
  1961                                     Cameroon   1380.509848  0.000270   
  3744                           Sub-Saharan Africa   1155.598604  0.000253   
  77                                           Iraq   2735.548508  0.000477   
  ...                                           ...           ...       ...   
  2323                                    Euro area   8176.246244  0.001881   
  2004                                     Colombia   1282.364618  0.001228   
  4287  East Asia & Pacific (excluding high income)    215.392022  0.000285   
  543                                         Spain   3270.405729  0.000822   
  975                                        Norway  15772.240907  0.001866   
  2771                                   South Asia    181.015595  0.000319   
  876                                        Latvia  13702.689470  0.003078   
  1462                                      Georgia    928.010823  0.006630   
  2473                                    St. Lucia   7577.209593  0.001093   
  3177                                 OECD members  18315.616212  0.002296   
  1931                                     Bulgaria   2169.004011  0.001560   
  2250                                     Zimbabwe    631.990604  0.000288   
  327                                         Italy  14187.774245  0.000912   
  1915                                     Bulgaria   1963.572676  0.001581   
  4087                    Latin America & Caribbean   6845.832331  0.002543   
  916                                        Malawi    146.761540  0.000050   
  281                                         Ghana    375.320435  0.000109   
  3497                               Macedonia, FYR   2240.139214  0.001018   
  50                                

### 2.1.3 ratio of female teachers in pre-primary and primary education
- Using `ratio of female teachers in pre-primary and primary education` as x axi and `GDP per capita (current US$)` as y axi. 
- Observation: `ratio of female teachers in pre-primary and primary education` and `GDP per Captia  (current US$)` have a good positive correlation. We hypothesize that developed countries tend to have more balanced female to male raito in teachers. 
The result also confirms our hypothesis. **Therefore, we can add it to our prediction model.**

In [0]:
%%bigquery --project $project_id q213
WITH female AS (
    SELECT R1.country_name, R1.year, (R1.value+R2.value) combined_value
    FROM
    (SELECT country_name, value, year
    FROM `bigquery-public-data.world_bank_intl_education.international_education`
    WHERE indicator_name = "Teachers in pre-primary education, female (number)") R1,
    (SELECT country_name, value, year
    FROM `bigquery-public-data.world_bank_intl_education.international_education`
    WHERE indicator_name = "Teachers in primary education, female (number)") R2
    WHERE R1.country_name = R2.country_name AND R1.year = R2.year
),

both AS (
    SELECT R1.country_name, R1.year, (R1.value+R2.value) combined_value
    FROM
    (SELECT country_name, value, year
    FROM `bigquery-public-data.world_bank_intl_education.international_education`
    WHERE indicator_name = "Teachers in pre-primary education, both sexes (number)") R1,
    (SELECT country_name, value, year
    FROM `bigquery-public-data.world_bank_intl_education.international_education`
    WHERE indicator_name = "Teachers in primary education, both sexes (number)") R2

WHERE R1.country_name = R2.country_name AND R1.year = R2.year
)

SELECT female.country_name, c1.value AS GDP, IF(both.combined_value != 0, ROUND(female.combined_value/both.combined_value, 2), 0) AS female_ratio, female.year
FROM 
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN female ON c1.country_name = female.country_name AND c1.year = female.year
  LEFT JOIN both ON female.country_name = both.country_name AND female.year = both.year

In [0]:
sampleq213 = q213.sample(5000)
alt.Chart(sampleq213).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("female_ratio:Q", axis=alt.Axis(title="female_ratio_in_pre-primary_and_primary_education"))     
)

Chart({
  data:                     country_name           GDP  female_ratio    year
  6213                     Lebanon   5372.065899          0.88  2006.0
  8956                      Panama   2848.950175          0.81  1984.0
  6533   Latin America & Caribbean   5075.128695          0.82  2005.0
  5690                 Congo, Rep.   1289.337837          0.50  2004.0
  2854                        None   4834.136723          0.00     NaN
  613                         None  15154.456873          0.00     NaN
  5712                      Belize   4324.876427          0.75  2007.0
  4078                        None   3807.324145          0.00     NaN
  5348                        None   2429.591085          0.00     NaN
  2700                        None    249.090254          0.00     NaN
  6609                     Burundi    260.479907          0.54  2011.0
  6137  Middle East & North Africa    518.641984          0.44  1973.0
  2742                        None    967.175850          0.00     NaN
  969                         None     99.265704          0.00     NaN
  8259              Czech Republic   3931.744463          0.96  1993.0
  8931          Iran, Islamic Rep.   2315.382036          0.56  1977.0
  2455                        None  23687.316893          0.00     NaN
  1443                        None   1445.706999          0.00     NaN
  4938                        None   2591.797116          0.00     NaN
  6871           Brunei Darussalam  14941.062399          0.49  1979.0
  6351                      Jordan   4066.940775          0.85  2014.0
  4071                        None   1639.850882          0.00     NaN
  4987                        None  11502.396813          0.00     NaN
  8248                    Bulgaria   3381.507837          0.96  2004.0
  8381                   Argentina   1366.354726          0.93  1971.0
  5184                        None  21901.057518          0.00     NaN
  8616                        Cuba   2741.110542          0.87  2000.0
  6167                      Mexico    729.743320          0.63  1971.0
  1805                        None    345.138132          0.00     NaN
  1949                        None    814.075287          0.00     NaN
  ...                          ...           ...           ...     ...
  6906                  Luxembourg  48179.420853          0.73  2001.0
  1307                        None   1427.102480          0.00     NaN
  6200                      Cyprus  27340.883816          0.88  2014.0
  7671                    Dominica   4924.922784          0.83  2001.0
  7230                    Suriname   5207.900020          0.92  2006.0
  216                         None  41819.870009          0.00     NaN
  8099                     Ukraine   2303.018831          0.99  2006.0
  3022                        None    503.498908          0.00     NaN
  5430                        None   1597.534644          0.00     NaN
  170                         None    915.775749          0.00     NaN
  4568                        None   2738.284723          0.00     NaN
  1170                        None  33228.692909          0.00     NaN
  3977                        None   5479.498064          0.00     NaN
  4155                        None   3848.569739          0.00     NaN
  275                         None   3018.008675          0.00     NaN
  5820                     Estonia  14638.604817          0.97  2010.0
  2553                        None     65.011416          0.00     NaN
  1196                        None   1389.719796          0.00     NaN
  4220                        None    314.746051          0.00     NaN
  7580                       Japan   2260.375947          0.58  1971.0
  395                         None   1164.612525          0.00     NaN
  8429         East Asia & Pacific   1163.155138          0.45  1980.0
  5704                        Cuba   2024.660040          0.75  1980.0
  313                         None   5853.932584          0.00     NaN
  1236    

### 2.1.4 ratio of female teachers in tertiary education
- Using `ratio of female teachers in tertiary education` as x axi and `GDP per capita (current US$)` as y axi. 
- Observation: `ratio of female teachers in tertiary education` and `GDP per Captia  (current US$)` have a good positive correlation. We hypothesize that developed countries tend to have more balanced female to male raito in teachers. 
The result also confirms our hypothesis.  **Therefore, we do also add it to our prediction model.**

In [0]:
%%bigquery --project $project_id q214
SELECT c1.country_name, c1.value AS GDP, IF(c3.value != 0, ROUND(c2.value/c3.value, 2), 0) AS female_ratio, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN 
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education`
   WHERE indicator_name = "Teachers in tertiary education programmes, female (number)") c2 ON c1.country_name = c2.country_name AND c1.year = c2.year
  LEFT JOIN 
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education`
   WHERE indicator_name = "Teachers in tertiary education programmes, both sexes (number)") c3 ON c1.country_name = c3.country_name AND c1.year = c3.year

In [0]:
sampleq214 = q214.sample(5000)
alt.Chart(sampleq214).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("female_ratio:Q", axis=alt.Axis(title="female_ratio_tertiary_education"))     
)

Chart({
  data:                                            country_name           GDP  \
  7115  Latin America & Caribbean (excluding high income)   1809.560876   
  8042        East Asia & Pacific (excluding high income)    162.667008   
  9013                                Lower middle income    459.520842   
  2741                                            Iceland  24651.589334   
  8482                                        Netherlands  39954.642216   
  8002                                        High income   7555.246957   
  9035  Middle East & North Africa (excluding high inc...   1607.588310   
  4205                                         Seychelles   2329.353358   
  152                                               World    868.350573   
  4118                                         Montenegro   7186.429787   
  783                                         Puerto Rico  25768.736048   
  6076                                East Asia & Pacific   3766.856127   
  9030  Latin America & Caribbean (excluding high income)   1545.859400   
  2378                                            Belgium  12932.860596   
  9121                                           Honduras   2242.707459   
  3642                                          Argentina  10276.260498   
  7681                                       Sierra Leone    226.908496   
  4317                                        Gambia, The    483.486301   
  6282                                              Japan  43440.367868   
  8350                                       Bahamas, The  11381.821560   
  3295                                           Honduras   1815.489496   
  8875                                               Togo    310.437014   
  1187                                              Chile   1116.870566   
  7332                                         South Asia    160.391093   
  890                                    Congo, Dem. Rep.    509.099879   
  7464                         Middle East & North Africa   8276.889368   
  8431                                              Qatar  28430.636355   
  4789                                      Liechtenstein   7354.102368   
  8617                                              World   1550.190596   
  1561                                              Samoa    706.276035   
  ...                                                 ...           ...   
  5259                                 Dominican Republic   2258.258540   
  8783                                              World  10163.902775   
  2136                                             Sweden   7198.271657   
  1483                                              Nepal    156.656353   
  2887                                            Liberia    388.266703   
  493                                             Uruguay   1440.152554   
  6448                                         South Asia    121.240477   
  6560                                              Chile  12860.177645   
  7289                                   Congo, Dem. Rep.    420.870490   
  7518                                      Middle income   4815.434956   
  7469                                         Kazakhstan   5291.575650   
  79                                                Benin    303.348898   
  7910                                            Bermuda  90849.586981   
  8888                                         Mauritania   1364.283926   
  5868                                       Turkmenistan   7962.365824   
  6542                         Middle East & North Africa   2739.136447   
  7810                                            Romania   2124.873613   
  579                                            Portugal   9978.301937   
  8090                                             Cyprus  10526.141770   
  6926                                     European Union  28838.506573   
  8549                                            Andorra  40619.711298   
  6623     

##2.2 Labor Population
Labor is a kind of outcome of education and we will explore the following index:
- Population dependency ratio

We hypothesize that the higher the "Population Depdendency Ratio", the more developed a country tends to be because developed countries suffer from aging population.

###2.2.1 Population Dependency Ratio
- Using "Population Depdendency Ratio" as x axi and "GDP per capita (current US$)" as y axi. In economics, geography, demography and sociology, the dependency ratio is an age-population ratio of those typically not in the labor force (the dependent part ages 0 to 14 and 65+) and those typically in the labor force (the productive part ages 15 to 64). It is used to measure the pressure on productive population.
- Observation: We hypothesize that the higher the "Population Depdendency Ratio", the more developed a country tends to be because developed countries suffer from aging population. Yes, the resulting table shows a strong **negative** correlation between popultion_dependency_ratio and GDP per captia. The distribution is even and the correlation is strong. **Therefore, we want to add this feature to our model.**

In [0]:
%%bigquery --project $project_id q221
SELECT c1.country_name, c1.value AS GDP, IF(c2.value!=0, (100-c2.value)/c2.value, 0) AS popultion_dependency_ratio, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
   LEFT JOIN
  (SELECT country_name,value, year, indicator_name FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Population, ages 15-64 (% of total)" ) c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:

sampleq221 = q221.sample(5000)
alt.Chart(sampleq221).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("popultion_dependency_ratio:Q", axis=alt.Axis(title="popultion_dependency_ratio"))     
)

Chart({
  data:                                      country_name           GDP  \
  7111                              Slovak Republic  10654.793707   
  7816                          Lower middle income    257.891702   
  5439                                   Luxembourg  52930.641152   
  4925                                    Mauritius   2973.206977   
  7408                            Brunei Darussalam  10711.866044   
  8319                    Latin America & Caribbean   1853.778814   
  1838                                       Latvia  12219.373790   
  3118                                      Ireland   6380.069479   
  3467                                      Namibia   2482.368620   
  3153                                      Ireland  61359.644769   
  2117                                       Rwanda    260.801691   
  3125                                      Ireland  48671.888119   
  2570                                      Belgium   3852.141729   
  5448                                   Luxembourg  47584.464392   
  4666                                    Argentina   2501.480753   
  1323                                       Belize   4849.997495   
  8013                         Syrian Arab Republic    337.039584   
  1924                                       Mexico   3655.597592   
  6448                                 Saudi Arabia  16472.166047   
  2356                                      Albania    865.302162   
  6405                                 OECD members   9304.488088   
  57                                           Cuba    653.232915   
  474                                         Chile   1296.892999   
  2249                                       Uganda     99.175747   
  7822                          Lower middle income    574.904220   
  2993                                      Germany  25488.519519   
  2696                                      Comoros    852.954308   
  5546                                   Mauritania    217.588040   
  4469                                     Slovenia  23437.472021   
  7481                           Dominican Republic    582.850032   
  ...                                           ...           ...   
  8786                                       Tuvalu   1369.074641   
  3217                                      Lao PDR    148.984408   
  5367                                   Kazakhstan   5291.575650   
  6348                                 Bahamas, The  11682.084965   
  2997                                      Germany   6609.753392   
  5636                                   Seychelles   7280.989621   
  7981                         Hong Kong SAR, China  26649.750802   
  3608                                      Senegal   1101.202117   
  6869                                United States  34620.928899   
  1016                                        Qatar  14047.052391   
  8993                                   San Marino  68758.368617   
  8521  East Asia & Pacific (excluding high income)   4010.464900   
  5582                                   Montenegro   1909.583957   
  5103                                    St. Lucia   3502.279151   
  5627                                   Seychelles    546.951061   
  2130                                       Serbia   2149.909404   
  4361                                     Pakistan    332.475957   
  8444       Heavily indebted poor countries (HIPC)    890.049442   
  6114                                  New Zealand  39416.358733   
  3193                                      Jamaica   4878.575791   
  4289                                     Mongolia   3694.082552   
  6175                                  Philippines   2951.071929   
  9088                               American Samoa  11865.963232   
  5716                                   South Asia    953.869449   
  2199                                       Turkey  10672.054821   
  8095                        Europe & Central Asia  

##2.3 Government Policy

It is undoubtable that goverment policies influence the GDP and we especially inspect those education policies because they show how much a government invest in its people. Developed countries generally tend to invest more than developing countries.
- Government expenditure on education as % of GDP (%)
- Duration of compulsory education (years)

###2.3.1 Government Expenditure on Education  
- Using "Government expenditure on education as % of GDP (%)" as x axi and "GDP per capita (current US$)" as y axi.
- Observation: As the expenditure on education by a goverment can somehow shows how much this goverment concerns about education, we try to find out if it has heavy influence on development level. `Government expenditure on education` should reflect the development level of an area. The resulting table shows a strong positive correlation between government expenditure on education and development level.  **Therefore, the  feature can  be added to our model.**


In [0]:
%%bigquery --project $project_id q231
SELECT c1.country_name, c1.value AS GDP, c2.value AS Gov_Exp_Edu, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Government expenditure on education as % of GDP (%)") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year AND c2.value < 100

In [0]:

sampleq231 = q231.sample(5000)
alt.Chart(sampleq231).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("Gov_Exp_Edu:Q", axis=alt.Axis(title="Gov_Exp_Edu"), scale = alt.Scale(domain = [0,15]))     
)

Chart({
  data:                                            country_name           GDP  \
  6606                                         Kazakhstan  12806.565108   
  9145  Latin America & Caribbean (excluding high income)   6556.496925   
  1819                                           Barbados  12868.787327   
  7741                                     Czech Republic   2878.719283   
  1938                                           Djibouti   1325.990724   
  474                                               Spain  13303.676131   
  1092                                             Zambia    633.517623   
  860                                              Malawi    122.886435   
  3939                                              Japan  38900.569306   
  5292                                            Ireland  62139.674952   
  2475                                         Azerbaijan    883.643997   
  3085                                     Czech Republic  18373.648998   
  1111                                             Zambia    691.317816   
  3866                                              Haiti    393.016303   
  3157                                    Kyrgyz Republic    721.768691   
  5267                                            Iceland   4047.619079   
  8938             Heavily indebted poor countries (HIPC)    323.229424   
  5218                                            Germany   9876.228232   
  7850                                    Solomon Islands    785.449710   
  4094                                              Qatar  15448.665477   
  2982                                       South Africa   2683.578385   
  1876                                           Cambodia   1028.419568   
  3217                                   Egypt, Arab Rep.   1045.943208   
  8721                              Virgin Islands (U.S.)  16752.277133   
  5650                                            Vanuatu   1080.222889   
  752                                              Israel   4295.747240   
  3187                                    Slovak Republic   8696.913242   
  1118                                             Zambia    341.905562   
  465                                               Qatar  21763.450976   
  477                                               Spain  15429.939422   
  ...                                                 ...           ...   
  5731                                           Bulgaria   7469.025247   
  6042                                           Paraguay   2000.911081   
  6006                                           Mongolia   1485.539626   
  750                                              Israel  13645.225342   
  1721                                            Senegal   1081.939254   
  4940                                            Bahrain   8706.725084   
  4390                                             Cyprus  15247.293289   
  4331                                             Bhutan    751.575772   
  3940                                              Japan  40855.175635   
  4944                                            Bahrain  12868.210997   
  495                                               Spain  13378.849842   
  2918                                        Yemen, Rep.    535.833052   
  5958                                           Kiribati   1587.057869   
  3678                                               Peru   6049.232578   
  7053                                        Isle of Man  21551.779359   
  777                                              Israel   9372.035791   
  5891                                           Honduras    798.818355   
  8650                              Europe & Central Asia  24970.975153   
  3455                              Sao Tome and Principe    810.860157   
  8775                           Central African Republic    103.409867   
  1795                                            Vanuatu   1353.934819   
  7551     

###2.3.2 duration of compulsory Education (years)
- Using "duration of compulsory Education (years)" as x axi and "GDP per capita (current US$)" as y axi.
- Observation: We hypothesize that the length of conpulsory education signals how much government is willing to invest in education, which tends to be the case in developed countries. However, we find that `duration of compulsory Education (years)`, thougth having a positive correlation with GDP per Captia, has a big variance along the y-axis. It means that the length of compulsory education is not a good indicator of the development level.  **Therefore, the feature can  NOT be added to our model.**

In [0]:
%%bigquery --project $project_id q232
SELECT c1.country_name, c1.value AS GDP, c2.value AS duration, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Duration of compulsory education (years)") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:
sampleq232 = q232.sample(5000)
alt.Chart(sampleq232).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("duration:Q", axis=alt.Axis(title="duration"))     
)

Chart({
  data:                                      country_name           GDP  duration  \
  560                                  South Africa   1201.332915       NaN   
  2012                                   Cabo Verde    456.462908       NaN   
  937                                 United States   8611.401839       NaN   
  9195                                  Puerto Rico  24898.338840      16.0   
  318                                         Italy   2662.326351       NaN   
  3335                                       Israel  12658.154059       NaN   
  3854                                        Chile   3362.169308       NaN   
  7190                                      Morocco   1721.973863       9.0   
  7557                                     Paraguay   3225.591754       9.0   
  1605                                      Iceland  14942.813996       NaN   
  2886                                    Singapore   8902.412337       NaN   
  5272                                  High income  29233.677036       NaN   
  5324                           Sub-Saharan Africa    646.294516       NaN   
  8680                                        Malta  23964.495514      11.0   
  6793                                       Malawi    280.367384       8.0   
  1102                           Dominican Republic    847.600633       NaN   
  3815                          Antigua and Barbuda   7296.551773       NaN   
  2274                         Hong Kong SAR, China   6208.226159       NaN   
  3758                                   Kazakhstan   1515.104059       NaN   
  7993                                        Spain  15323.611398      10.0   
  5263                                      Lesotho    407.809391       NaN   
  5244                               European Union  19816.237163       NaN   
  3116                          East Asia & Pacific   2530.296808       NaN   
  3955                               United Kingdom  18389.019568       NaN   
  2144                                      Morocco    748.866787       NaN   
  6064                                   Bangladesh    835.789340       5.0   
  8838                                 Bahamas, The  23719.107882      12.0   
  1704                             Congo, Dem. Rep.    463.685936       NaN   
  3777                                Cote d'Ivoire    847.295846       NaN   
  8147                                         Chad    712.184769      10.0   
  ...                                           ...           ...       ...   
  5732                                      Vanuatu   3275.091684       NaN   
  4453                                         Oman   6261.719017       NaN   
  6005                                      Lao PDR    324.845050       5.0   
  2141                                      Vanuatu    886.315220       NaN   
  7471                                 Saudi Arabia  20037.832339       9.0   
  4279                                      Ireland  19181.400481       NaN   
  516                                    Madagascar    231.436186       NaN   
  1612                                        Japan   9416.630280       NaN   
  5356                                      Eritrea    287.422224       NaN   
  7091                                Guinea-Bissau    309.486749       9.0   
  9045                                       Poland  12421.318909      12.0   
  4932                                       Uganda    291.986407       NaN   
  3045                                       Norway  24207.281469       NaN   
  4857                                    Indonesia   1132.562479       NaN   
  7490                               Macedonia, FYR   4793.292959       9.0   
  5772                          Low & middle income   4395.298705       NaN   
  8862                          St. Kitts and Nevis  13538.928580      12.0   
  1357                    Latin America & Caribbean   1837.387378       NaN   
  1431                              

##2.4 Unemployment 
We hypothesize that the higher the "unemployment_rate", the less developed a country tends to be because in developed countries most people are employed/productive.
  - Unemployment, total (% of total labor force)

###2.4.1 Unemployment Rate
- Using "unemployment_rate" as x axi and "GDP per capita (current US$)" as y axi. In economics, unemployment_rate is the proportion of employable populatin that have a job. 
- Observation:  Yes, the resulting table shows a slight **negative** correlation between popultion_dependency_ratio and GDP per captia. The distribution is even but the correlation is not strong. **Therefore, we do NOT want to add this feature to our model.**

In [0]:
%%bigquery --project $project_id q241
SELECT c1.country_name, c1.value AS GDP, c2.value AS unemployment_rate, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Unemployment, total (% of total labor force)") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:
sampleq241 = q241.sample(5000)
alt.Chart(sampleq241).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("unemployment_rate:Q", axis=alt.Axis(title="unemployment_rate"))     
)

Chart({
  data:                   country_name           GDP  unemployment_rate  year
  3147               Gambia, The    322.446305                NaN  1989
  2665                  Cameroon   1024.387656                NaN  1986
  8155    Bosnia and Herzegovina   3404.321698          31.100000  2006
  705                       Togo    237.814016                NaN  1974
  961                Puerto Rico   2946.461953                NaN  1976
  815        East Asia & Pacific    647.331204                NaN  1975
  3767                    Kosovo   2788.479464                NaN  2007
  2279       St. Kitts and Nevis   2267.424326                NaN  1984
  1367                   Jamaica   1137.077587                NaN  1979
  6862        Sub-Saharan Africa   1705.276451           7.737022  2011
  5342              Turkmenistan    622.371080           8.700000  1994
  2631       Lower middle income    420.000853                NaN  1986
  5731  Central African Republic    271.855117           6.200000  1999
  3615                    Monaco  82534.873767                NaN  2000
  7813                     Libya   7040.701924          19.799999  1991
  4836                    Kuwait  15391.345736           0.700000  1999
  846                      Gabon   3320.824694                NaN  1975
  6725     Sao Tome and Principe   1129.754961          14.300000  2010
  6372                     Kenya    452.984807          10.400000  1997
  8932                  Paraguay   1408.527976           7.400000  2004
  2710                    Guyana    468.104341                NaN  1987
  7989                   Bahrain  10672.183944           1.400000  1997
  2326                    Malawi    175.179625                NaN  1984
  1170               Gambia, The    250.253695                NaN  1977
  1512                 Greenland   9483.173076                NaN  1980
  7508                Madagascar    443.906100           1.300000  2012
  7877                   Bolivia   2645.227753           2.300000  2012
  8680                  Honduras    687.481420           4.400000  1996
  417         Dominican Republic    417.505789                NaN  1972
  6798       Lower middle income    579.620385           5.238623  1996
  ...                        ...           ...                ...   ...
  3704                  Kiribati   1130.602806                NaN  2004
  6071                   Iceland  32198.908579           2.200000  1999
  1101                 Australia   7769.596680                NaN  1977
  316              New Caledonia   4031.016039                NaN  1972
  4426                      Peru   2448.143899           9.000000  2004
  9007     Virgin Islands (U.S.)  31947.078688           8.800000  2003
  2161       Lower middle income    412.959867                NaN  1983
  1932               Switzerland  17478.655793                NaN  1982
  7875                   Vietnam   1164.612525           2.300000  2008
  3766                     Palau   9682.198250                NaN  2007
  6743                    Serbia   5426.897946          15.300000  2016
  3410  Central African Republic    490.074562                NaN  1990
  5443          Papua New Guinea    965.266188           2.600000  1992
  5977                   Namibia   1713.047594          21.400000  2002
  4895                   Romania   2124.873613           8.100000  2002
  5583      United Arab Emirates  33072.575166           4.200000  2009
  5990              South Africa   3288.289972          25.400000  1991
  8856                   Finland  53401.314873           6.400000  2008
  386                High income   3545.517994                NaN  1972
  6421                    Guyana   1045.588610          11.400000  2004
  5294                  Portugal  19821.444627           7.600000  2006
  4002               Switzerland  38538.990053           2.500000  2001
  888                      Qatar  18893.102304                NaN  1976
  1623              Burkin

##2.5 Learning Outcome
Learning outcomes (such as literacy rate) are important indicators of a country's dvelopment level. Most developed countries have high literacy rate and developeding countries tend to have lower rates. 

- PIAAC: Mean Adult Numeracy Proficiency. Total
- PIAAC: Mean Adult Literacy Proficiency. Total

About two learning outcomes, although their correlations are good, there are not enough tuples. Therefore, we chose not to use them in the end. 

###2.5.1 Numeracy Proficiency and Literacy Proficiency and GDP
- Trying to find out  the relationship between
PIAAC: Mean Adult Numeracy Proficiency. Total,   PIAAC: Mean Adult Literacy Proficiency. Total and GDP. Drawing these two lines in one graph, setting them as x axi and GDP as y axi. 
- Observation: literacy and numeracy should reflect the development level of an area. Red points represent `Literacy_Proficiency` and blue points represent `Numeracy_Proficiency`.The resulting table only contains 30 rows out of 9000 rows that do not contain any NULL value although there is a positive trend that can be seen in the graph.  **Therefore, the two features can NOT be added to our model.**

In [0]:
%%bigquery --project $project_id q251
WITH proficiency AS(
SELECT c1.country_name, c1.value AS Numeracy_Proficiency, c2.value AS Literacy_Proficiency, c1.year
FROM
  (SELECT country_name,value,year 
  FROM `bigquery-public-data.world_bank_intl_education.international_education` 
  WHERE indicator_name = "PIAAC: Mean Adult Numeracy Proficiency. Total") c1
FULL JOIN
  (SELECT country_name,value,year 
  FROM `bigquery-public-data.world_bank_intl_education.international_education` 
  WHERE indicator_name = "PIAAC: Mean Adult Literacy Proficiency. Total") c2
ON c1.country_name = c2.country_name
ORDER BY c1.country_name)

SELECT c1.country_name, c1.value AS GDP, Numeracy_Proficiency, Literacy_Proficiency, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN proficiency
ON c1.country_name = proficiency.country_name AND c1.year = proficiency.year


In [0]:
sampleq251 = q251.sample(5000)
line1 = alt.Chart(sampleq251).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP")),
    alt.X("Numeracy_Proficiency:Q", axis=alt.Axis(title="Proficiency"),scale = alt.Scale(domain= [200,300])),
    
)

line2 = alt.Chart(sampleq251).mark_point(color = 'red').encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP")),
    alt.X("Literacy_Proficiency:Q", axis=alt.Axis(title="Proficiency"),scale = alt.Scale(domain= [200,300])) 
)

line1+line2

LayerChart({
  layer: [Chart({
    data:                                            country_name           GDP  \
    563                                            Cambodia     94.383276   
    4747                                           Cameroon    764.784607   
    48                                               Jordan    372.093731   
    5819                                           Colombia   2395.856551   
    3540                                           Pakistan    410.474021   
    5077                                             Panama   3974.650657   
    797                                          Bangladesh    272.745198   
    606                                             Belgium   4927.195923   
    5171                                         Bangladesh    395.297461   
    8227                                        High income  42012.695921   
    6644                                            Finland  38969.171632   
    3109                                             Malawi    174.849828   
    5446                                     Czech Republic   6011.615220   
    5622                                              Qatar  28430.636355   
    38                                               France   2862.469268   
    2086                                        High income   9739.550557   
    7752                                           Ethiopia    341.309909   
    4561             Heavily indebted poor countries (HIPC)    311.892723   
    1707                                             Uganda    103.424469   
    119                                          Seychelles    343.881182   
    5911                                           Tanzania    308.056553   
    7106                                        Timor-Leste    498.849140   
    3200                                       South Africa   3584.101364   
    6359                              Europe & Central Asia  18071.333756   
    9011                                           Colombia   5805.605385   
    8400                             Bosnia and Herzegovina   5042.582213   
    4835                                   Macao SAR, China  17957.946380   
    340                                    Congo, Dem. Rep.    292.314010   
    5280                                      Liechtenstein  81116.439165   
    4                                                Poland  13143.521219   
    ...                                                 ...           ...   
    1534                                            Finland  11232.274564   
    1911                                         Luxembourg  13034.811660   
    6341                                         Montenegro   3380.199535   
    2921                                              Benin    346.736038   
    6670                                            Denmark  48799.820370   
    2863                                          Singapore   7531.250196   
    8882                                   Marshall Islands   3390.910292   
    8112                                   Macao SAR, China  66813.349741   
    3581                                            Uruguay   3577.910095   
    8116                                               Iraq   5854.614497   
    4123                     St. Vincent and the Grenadines   2676.788664   
    4091                                        Korea, Rep.   8740.945603   
    2227                                       Saudi Arabia   9581.511759   
    4606                                         Kazakhstan   1350.333866   
    755                                           Indonesia    215.529406   
    2189                                           Cameroon    781.561927   
    3788                                         Kazakhstan   1515.104059   
    6717                              Sao Tome and Principe    810.860157   
    4921  Latin America & Caribbean (excluding high income)   4341.901082   
    7310                            

##2.6 Education Technology
- Personal computers (per 100 people) 
- Internet users (per 100 people)

We hypothesize that more advanced the education technology are accompanied with higher development level.

###2.6.1 Personal computers (per 100 people)
- Using `Personal computers (per 100 people)` as x axi and `GDP per capita (current US$)` as y axi. 
- Observation: `Personal computers (per 100 people)` and `GDP per Captia  (current US$)` have a positive correlation. The hypothesis is that The use of personal computers signals the development level of an area. The result also confirms our hypothesis that developed areas tend to have more personal computers. However, the resulting table has many NULL values because `Personal computers (per 100 people)` is surveyed in limited year range and countries. The distribution of data is also not even across x-axis. **Therefore, we decide to NOT add it to our prediction model.**

In [0]:
%%bigquery --project $project_id q261
SELECT c1.country_name, c1.value AS GDP, c2.value AS Personal_computers, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Personal computers (per 100 people)") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:
sampleq261 = q261.sample(5000)
alt.Chart(sampleq261).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("Personal_computers:Q", axis=alt.Axis(title="Personal_computers (per 100 people)"))     
)

Chart({
  data:                                            country_name            GDP  \
  6163                                             Monaco   91654.119007   
  1123                                         Arab World    2204.172534   
  4448                                             Kuwait   17364.399477   
  637                                      United Kingdom   23013.458820   
  7561                                          Singapore   38577.558216   
  3880                                           Thailand     445.319496   
  7899                                         Madagascar     454.963464   
  2409       Least developed countries: UN classification     426.107798   
  6863                                             Kosovo    2135.332847   
  8277                                            Tunisia    4137.548140   
  2798                                              Chile     954.249117   
  1665                                              Kenya     401.776361   
  1203                                              Japan   36026.556075   
  6411                                              Samoa    1309.916028   
  2840                                              Benin     114.556596   
  6617                                            Burundi     159.175528   
  1214                                Upper middle income    1813.324161   
  738         East Asia & Pacific (excluding high income)     878.445309   
  3810                                  Equatorial Guinea     421.553368   
  521                                 Upper middle income    1582.388570   
  4518  Latin America & Caribbean (excluding high income)    2321.162867   
  7665                               United Arab Emirates   35049.148317   
  1775                                            Vanuatu    1353.934819   
  6359                                              Haiti     282.422701   
  546                                             Nigeria     171.669746   
  6769                             Bosnia and Herzegovina    1461.750520   
  3959                                         Bangladesh     172.414696   
  860                                      United Kingdom   26621.480059   
  560                                                Oman    6013.166677   
  8545                                              Niger     416.140084   
  ...                                                 ...            ...   
  8191                                             Uganda     637.130009   
  7790                                        Isle of Man   73935.678995   
  3004                                              Benin     112.570089   
  7794                                          Swaziland    3690.239228   
  2450                                             Latvia    7558.742006   
  3913                                            Grenada     792.762369   
  2852                                             Kuwait    3848.569739   
  8991                                 Iran, Islamic Rep.    5219.109408   
  7013                                      Liechtenstein  113983.167762   
  3166                                       South Africa     899.801867   
  2987                                             Monaco   13813.300504   
  8671                                             Guyana    4031.532007   
  7481                                            Uruguay    9415.170386   
  6778                                      New Caledonia   12579.595106   
  6839                                          Greenland   24801.659030   
  3682                                             Monaco   28810.873014   
  5849                                         Mozambique     189.624538   
  2338                                        Switzerland   53340.147656   
  8382                                Antigua and Barbuda   12194.608761   
  8469                                          Swaziland    3587.000316   
  1410                            

###2.6.2 Internet users (per 100 people)
- Using `Internet users (per 100 people)` as x axi and `GDP per capita (current US$)` as y axi. 
- Observation: `Internet users (per 100 people)` and `GDP per Captia  (current US$)` have a positive correlation. The hypothesis is that The use of Internet signals the development level of an area. The result also confirms our hypothesis that developed areas tend to have more internet use. The resulting table also has way less NULL values and is more evenly distributed than the computer use one. **Therefore, we decide to add it to our prediction model.**

In [0]:
%%bigquery --project $project_id q262
SELECT c1.country_name, c1.value AS GDP, c2.value AS Int_user, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Internet users (per 100 people)") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:
sampleq262 = q262.sample(5000)
alt.Chart(sampleq262).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("Int_user:Q", axis=alt.Axis(title="Internet users (per 100 people)"))     
)

Chart({
  data:                                            country_name           GDP  \
  1357                                               Oman   8601.185906   
  2673                                             Turkey   8034.606676   
  4550                               United Arab Emirates  39101.746890   
  8828                                             Kosovo   3283.211938   
  6632                                            Bolivia   1031.516161   
  4818                             Bosnia and Herzegovina   4808.405425   
  6729                                             France  10505.735472   
  401                                         Philippines   1061.347868   
  3906                                              World  10551.742820   
  173   Latin America & Caribbean (excluding high income)   3237.796608   
  5794                                   Congo, Dem. Rep.    409.548544   
  5777                                            Bermuda   7261.278195   
  6627         Sub-Saharan Africa (excluding high income)    703.001898   
  6078                                              Japan   8776.408455   
  4741                     St. Vincent and the Grenadines   7006.596196   
  7953                                        Korea, Rep.   5736.903807   
  3552                                         Bangladesh    757.671757   
  1848                                            Belarus   1479.383142   
  6871                                             Belize   1212.922437   
  5270        East Asia & Pacific (excluding high income)    132.172416   
  6785                              Europe & Central Asia   4852.975301   
  542                                        Bahamas, The  12717.150005   
  5545                                        New Zealand   4610.570426   
  7170                                            Andorra   7728.906695   
  1220                                            Germany  23718.746699   
  5494                                              Japan   4331.400905   
  1047                                             Brazil   3469.503972   
  7649                                Trinidad and Tobago   4014.047120   
  5827                                              Benin    208.656154   
  2472                                            Georgia   1530.057521   
  ...                                                 ...           ...   
  5952                                             Belize    858.828081   
  4093                                              Japan  40454.447458   
  4320                                             Panama  12593.737042   
  3272                                Upper middle income   5324.839677   
  3638                                            Germany  46810.327959   
  3749                                            Armenia   3526.978143   
  7378                                            Uruguay   1939.966701   
  7765                                            Bolivia    697.370560   
  8502                                            Vietnam    229.954797   
  4129                                        Yemen, Rep.   1580.181601   
  7922                                              World   3867.923794   
  8732                                         Montenegro   1909.583957   
  4380                                         Uzbekistan   2050.448414   
  5367                                      Middle income    308.339062   
  6808                                              Spain   5145.694384   
  1053                                              World   5384.311328   
  3122                                             Serbia   6701.773913   
  4598                                      North America  55153.758209   
  6923                                              Ghana    341.087217   
  6544                                            Uruguay   3764.293025   
  655                                           Argentina   8172.664323   
  689      

##2.7 Attainment 
- Barro-Lee: Percentage of population age 15+ with tertiary schooling. Completed Tertiary
- School life expectancy, primary to tertiary, both sexes (years) 
- Gross enrolment ratio, primary to tertiary, both sexes (%)
We hypothesize that the better the school attains the students, the more developed country the school tends to be. In many developing countries, students have to drop out of school to support their family. 

###2.7.1 Tertiary Schooling and GDP Per Capita
- Using "Barro-Lee: Percentage of population age 15+ with tertiary schooling. Completed Tertiary" as x axi and "GDP per capita (current US$)" as y axi. Both of them are chosen from 1970 to 2010 every 5 years. 
- Observation: `Percentage of population age 15+ with tertiary schooling` is positively correlated with `GDP per Captia`. GDP per Captia is measured annually but `Percentage of population age 15+ with tertiary schooling` is measured every 5 years.  This positive correlation is strong up to 10% and becomes weaker/more obscure above 10%. The left join between the two tables leads to many NULL values because the series is not done annually, thus there are many NULL values in the resulting table. **Therefore, we decide NOT to include this as a feature.**



In [0]:
%%bigquery --project $project_id q271
SELECT c1.country_name, c1.value AS GDP, c2.value AS Tertinary_Percentage, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Barro-Lee: Percentage of female population age 15+ with tertiary schooling. Completed Tertiary") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:
sampleq271 = q271.sample(5000)

alt.Chart(sampleq271).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("Tertinary_Percentage:Q", axis=alt.Axis(title="Tertinary_Percentage"))     
)

Chart({
  data:                                            country_name           GDP  \
  2671                                             Zambia    633.517623   
  4336                                     European Union  17794.681822   
  6412                                             Turkey   4718.456754   
  542                                              France  21795.237825   
  6232                                          Indonesia    957.780643   
  2979                                             Guyana    628.197689   
  2626                                          Greenland   8544.058329   
  1010                                            Croatia  13505.745863   
  8769                                           Cameroon   1353.924490   
  3938                                             Brazil   2901.285449   
  5750                                              Samoa   1489.647875   
  4134                                             Turkey   2735.710807   
  7320                                            Uruguay   7009.697046   
  3427         Sub-Saharan Africa (excluding high income)    597.062670   
  5513                                Lower middle income    518.556810   
  49                                          Philippines    186.768760   
  985                                              Panama   4916.548860   
  1600                                             Kuwait   5952.861796   
  2245                                            Germany   9446.166785   
  8709                                           Cambodia   1098.687123   
  2327                                             Jordan   1422.703959   
  1367                                           Botswana    222.469450   
  1677                                             Belize    786.069092   
  2768                                        El Salvador    719.295494   
  4379                                      New Caledonia  16261.296928   
  8170             Heavily indebted poor countries (HIPC)    843.869019   
  7044                                             Brazil   5860.145975   
  3085                                          Guatemala   1177.436451   
  7449                                      Cote d'Ivoire   1242.431044   
  2484                                             Bhutan    331.531227   
  ...                                                 ...           ...   
  2462                                Antigua and Barbuda   1789.589568   
  5810                                         Azerbaijan    655.097433   
  7478                                           Djibouti   1214.077118   
  899                                            Zimbabwe    444.760508   
  6422                                    Channel Islands  48226.396677   
  3276                                              Malta   4194.653939   
  5934                                           Malaysia   3915.115046   
  826                                                Mali    269.348383   
  2125                                              World   1723.172643   
  1065                                         Kazakhstan   9070.649972   
  7521                                            Ecuador   4274.952065   
  9079                                         Seychelles  15075.719437   
  3462                                         Cabo Verde    724.094307   
  6004                                              Kenya    401.776361   
  7237                                        High income  38546.871261   
  3082                                              Kenya    326.936463   
  3715                                           Thailand   1123.011814   
  494                                              Israel  12658.154059   
  260                                       United States  12597.667510   
  4597  Middle East & North Africa (excluding high inc...   1192.908453   
  63                                             Zimbabwe    364.054360   
  8589     

###2.7.2 School life expectancy, primary to tertiary
- Using `School life expectancy, primary to tertiary, both sexes (years)` as x axi and `GDP per capita (current US$)` as y axi. 
- Observation: `School life expectancy, primary to tertiary, both sexes (years)` and `GDP per Captia  (current US$)` have a strong positive correlation. This makes sense because developed countries tend to provide longer education to people. **Therefore, we want to include this as a feature.**

In [0]:
%%bigquery --project $project_id q272
SELECT c1.country_name, c1.value AS GDP, c2.value AS expectancy, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
  LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "School life expectancy, primary to tertiary, both sexes (years)") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:
sampleq272 = q272.sample(5000)
alt.Chart(sampleq272).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("expectancy:Q", axis=alt.Axis(title="expectancy"))     
)

Chart({
  data:                   country_name           GDP  expectancy  year
  5532                     Haiti    462.480652         NaN  2000
  5655                     Palau   6116.273812         NaN  1996
  796                     Brazil   3059.587582   14.014270  2003
  4643       Low & middle income   1198.908447    8.913336  1997
  8999     Micronesia, Fed. Sts.   2029.289159         NaN  1998
  8682         Brunei Darussalam   1455.308336         NaN  1971
  6265                   Algeria   2223.697344         NaN  1981
  96                        Iraq   1847.896567    8.922390  1978
  7494                 Singapore  54431.161990         NaN  2012
  8709         Equatorial Guinea  21451.886171         NaN  2011
  261                      Chile  14817.377777   16.335600  2014
  4294           Slovak Republic  13139.032177   14.487300  2006
  1846                   Georgia    670.461105   10.934810  1996
  6647                   Ireland  63861.921982         NaN  2016
  6603                   Grenada   2759.681938         NaN  1989
  5565                     Japan  35865.655934         NaN  1993
  8428             Venezuela, RB  10741.576384         NaN  2011
  5986                    Guyana    452.389353         NaN  1991
  1800                   Finland   7074.356530   13.021630  1977
  1129                    Mexico   5777.231681   11.391010  1999
  1659                   Burundi     85.047000    1.545490  1973
  4040             North America   9414.663527   13.326318  1977
  5665                     Palau   4970.070213         NaN  1994
  1941                   Ireland   2082.956898   10.804190  1972
  601                      Niger    258.046387    3.833440  2006
  7290                  Tanzania    296.340954         NaN  1998
  9113  Central African Republic    397.148047         NaN  2007
  4385          Egypt, Arab Rep.   2291.667062   12.179320  2009
  2766                  Thailand   5941.840710   16.161381  2014
  5715                     Samoa    772.207028         NaN  1990
  ...                        ...           ...         ...   ...
  598                      Niger    276.129989    1.765420  1983
  8163              Sierra Leone    406.375918         NaN  2008
  4817      United Arab Emirates  23612.745197   10.272380  1989
  8859       St. Kitts and Nevis   1123.387580         NaN  1978
  8706         Equatorial Guinea    141.322703         NaN  1983
  4156            Czech Republic   6609.205530   14.348320  2001
  3685               Netherlands  51241.315617   16.769430  2007
  5673                     Palau   6333.405312         NaN  1998
  7764                Mauritania    473.732776         NaN  1981
  2819                  Zimbabwe   1077.965350    9.014590  1981
  2159                   Nigeria    300.609008    7.600120  1999
  1814                   Finland  24253.250425   17.725281  2000
  26                        Cuba   1224.423039    9.911500  1974
  5726                     Sudan    427.177238         NaN  1978
  865                     France  10505.735472   12.786720  1982
  3050                 Nicaragua    243.561262    7.569730  1990
  5472                     Gabon   8754.113922         NaN  2010
  8539          Egypt, Arab Rep.   1258.997552         NaN  1998
  622                      Qatar  27385.770575   12.525480  1982
  3206                Costa Rica   1734.436062    9.701540  1979
  134                       Oman   6029.169254    9.201420  1993
  4588       East Asia & Pacific   3784.780623   10.140820  1999
  8771        Dominican Republic    968.792626         NaN  1979
  3007                 Lithuania  11984.868570   16.732910  2010
  5631                     Niger    158.405597         NaN  2000
  2355                  Bulgaria   7853.335191   15.040370  2014
  4558        West Bank and Gaza   2960.778004   12.843440  2014
  1041                    Jordan   1929.858724   11.931630  1988
  2261                   Ukraine   2303.018831   14.794290  2006
  4512        Sub-Sah

###2.7.3 Gross enrolment ratio, primary to tertiary
- Using `Gross enrolment ratio, primary to tertiary, both sexes (%)` as x axi and `GDP per capita (current US$)` as y axi. 
- Gross Enrollment Ratio (GER) or Gross Enrollment Index (GEI) is a statistical measure used in the education sector, and formerly by the UN in its Education Index, to determine the number of students enrolled in school at several different grade levels (like elementary, middle school and high school), and use it to show the ratio of the number of students who live in that country to those who qualify for the particular grade level.
- Observation: `Gross enrolment ratio, primary to tertiary, both sexes (%)` and `GDP per Captia  (current US$)` have a strong positive correlation. It is worth noting that the enrollment rate can be over 100% if enrolled students are more than expected enrolled students. It is reasonable because in developed areas people compete for the best education resources, causing the enrollment rate to be higher. This is different from the school life expentancy above and provides a different perspective about education. **Therefore, we should include this one as a feature too.**

In [0]:
%%bigquery --project $project_id q273

SELECT c1.country_name, c1.value AS GDP, c2.value AS GER, c1.year
FROM  
  (SELECT country_name, value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "GDP per capita (current US$)" ) c1
   LEFT JOIN
  (SELECT country_name,value, year FROM `bigquery-public-data.world_bank_intl_education.international_education` WHERE indicator_name = 
  "Gross enrolment ratio, primary to tertiary, both sexes (%)") c2
ON c1.country_name = c2.country_name AND c1.year = c2.year

In [0]:
sampleq273 = q273.sample(5000)

alt.Chart(sampleq273).mark_point().encode(
    alt.Y("GDP:Q", axis=alt.Axis(title="GDP"),scale=alt.Scale(type='log')),
    alt.X("GER:Q", axis=alt.Axis(title="Gross Enrollment Rate"))     
)

Chart({
  data:                country_name            GDP        GER  year
  3472            Korea, Rep.   12782.525535  94.136589  2002
  1344                 Turkey     558.421564  50.137562  1972
  6567               Maldives    8384.252877        NaN  2013
  965                  Israel   33689.838534  93.898407  2011
  3874          Venezuela, RB    3232.524276  73.525162  2003
  7275             San Marino   65035.960499        NaN  2004
  7899          Liechtenstein  104994.018302        NaN  2005
  7097             Bangladesh     757.671757        NaN  2010
  6772              Euro area    3018.225027        NaN  1972
  7239             Mauritania     477.476102        NaN  2000
  6260                Ukraine    2185.728031        NaN  2016
  6858              Guatemala    2256.567240        NaN  2006
  3845          United States   28782.175020  93.432579  1995
  8462     Sub-Saharan Africa     539.859672        NaN  1993
  7251             Montenegro    7318.742449        NaN  2011
  6013                Grenada    2410.286538        NaN  1988
  4277    East Asia & Pacific    3738.690349  65.461830  2001
  8823  Micronesia, Fed. Sts.    1756.185104        NaN  1992
  2562               Malaysia    7269.171140  69.140030  2007
  7451            High income    9596.756629        NaN  1980
  6423               Colombia    2395.856551        NaN  2001
  3270             Seychelles    8331.261997  66.456749  2002
  8617    St. Kitts and Nevis    8700.348672        NaN  1999
  864                  France   24799.296010  92.455566  1999
  8377     Dominican Republic    4647.310359        NaN  2007
  7707           Sierra Leone     173.820399        NaN  1987
  6119                Liberia     415.036196        NaN  2012
  4935                  Kenya     697.006639        NaN  2006
  366                   India     396.014612  51.493401  1996
  5549                 Sweden   51949.271432        NaN  2016
  ...                     ...            ...        ...   ...
  2994              Sri Lanka    3350.521375  77.789017  2012
  857                  France   11110.559768  74.711479  1981
  2272                Uruguay    6316.269940  76.768288  1996
  2517               Kiribati    1015.038605  77.248947  2003
  5465                 Malawi      63.105473        NaN  1970
  3642            Switzerland   88415.628061  86.696114  2011
  8721   Hong Kong SAR, China    1106.469717        NaN  1971
  3837          United States   51450.122295  97.278473  2012
  1506                Austria    5678.386638  74.451942  1976
  4107       Egypt, Arab Rep.    3181.441708  75.542572  2012
  5169                  World    5350.341673        NaN  1997
  4699                   Iraq    6703.074737        NaN  2014
  540                   Malta    5083.669139  67.999458  1987
  1292                 Serbia    6353.826383  83.547150  2013
  4892                  Haiti     674.756415        NaN  2008
  8478    Antigua and Barbuda    9932.029681        NaN  2000
  651                   Spain   15429.939422  88.647171  1995
  3385            Congo, Rep.     283.119039  56.621208  1972
  4636                   Chad     190.835983        NaN  1999
  3938         Macedonia, FYR    4698.689476  70.360161  2012
  8600    St. Kitts and Nevis    8235.563259        NaN  1998
  6798              Greenland   19004.107291        NaN  2000
  8164       Congo, Dem. Rep.     252.843045        NaN  2006
  5796                Bermuda   66111.725227        NaN  2003
  5702                Andorra   36038.267604        NaN  2015
  7984          New Caledonia    5249.053600        NaN  1984
  1669                Croatia   14157.144162  81.750183  2009
  5143                  Tonga    1120.256771        NaN  1989
  6517               Honduras     278.615013        NaN  1972
  330                   Gabon    4407.284354  74.359947  1984
  
  [5000 rows x 4 columns],
  encoding: EncodingWithFacet({
    x: X({
      axis: Axis({
        title: 'Gross Enrollment Rate'
      }),
 

##2.8 Conclusion 
- According to the graphs above, which attributes have strong relationship with income level? So that we could use such attributes to predict the income level of a country. 


**Based on the visualizaion analysis, the following features meet those criteria: ** 

1.   have strong relatonship with GDP per capita
2.   have enough years and countries to JOIN with labeled data
3.   are evely distributed in the correlation graph
4.   are diverse / different from each other


The 9 features are:

- proportion of preprimary and primary teachers in the whole population
- proportion of tertiary teachers in the whole population
- female-to-male ratio of preprimary and primary teachers
- female-to-male ratio of tertiary teachers
- population dependency ratio
- Government expenditure on edicatoin
- Internet users (per 100 people)
- School life expentancy
- gross enrollment rate

So we try to use these features to train our model predict
The reasones why we drop some features are explained individually at the beginning of each 2.1-2.7 section. They reasons tend to be: those features are 

1. too few 
2. have weak relationship with GDP per captia. 

### Save queries of the chosen feature into tables for later easy access

In [0]:
q211.to_gbq("feature_tables.Preprimary_and_primary_proportion","rapid-snowfall-218803")
q212.to_gbq("feature_tables.tertiary_proportion","rapid-snowfall-218803")
q213.to_gbq("feature_tables.Preprimary_and_primary_female_to_male_ratio","rapid-snowfall-218803")
q214.to_gbq("feature_tables.tertiary_female_to_male_ratio","rapid-snowfall-218803")
q221.to_gbq("feature_tables.popultion_dependency_ratio","rapid-snowfall-218803")
q231.to_gbq("feature_tables.Government_exp_on_edu","rapid-snowfall-218803")
q262.to_gbq("feature_tables.Internet_users","rapid-snowfall-218803")
q272.to_gbq("feature_tables.School_life_expectancy","rapid-snowfall-218803")
q273.to_gbq("feature_tables.gross_enrollment_rate","rapid-snowfall-218803")

#3. Predictions (20%)


## 3.1 Create a dataset


In [0]:
# Run this cell to create a dataset to store your model

model_dataset_name = 'edu_dataset'
dataset = bigquery.Dataset(client.dataset(model_dataset_name))
dataset.location = 'US'
client.create_dataset(dataset)

##3.2 Display 10 instances of the resulting table
 
 The resulting table makes sense. Despite some columns have some 0 values, it is reasonable and result from multiple left join because some feature tables can miss certain countries and years in their surveys.

In [151]:
%%bigquery --project $project_id
SELECT
  IF(c1.GDP < 12000 , 0, 1) AS label,
  IFNULL(c1.percent,0) AS primary_teacher_percent,
  IFNULL(c2.female_ratio, 0) AS primary_female_male_ratio,
  IFNULL(c3.popultion_dependency_ratio, 0) AS popultion_dependency_ratio,
  IFNULL(c4.Gov_Exp_Edu, 0) AS Gov_Expenditure_Edu,
  IFNULL(c5.Int_user, 0) AS Internet_user_percent,
  IFNULL(c6.expectancy, 0) AS school_life_expectancy,
  IFNULL(c7.GER, 0) AS gross_enrollment_rate,
  IFNULL(c8.percent,0) AS tertiary_teacher_percent,
  IFNULL(c9.female_ratio, 0) AS tertiary_female_male_ratio
FROM `feature_tables.Preprimary_and_primary_proportion` c1 
LEFT JOIN  `feature_tables.Preprimary_and_primary_female_to_male_ratio` c2 ON c1.country_name = c2.country_name AND c1.year = c2.year
LEFT JOIN  `feature_tables.popultion_dependency_ratio` c3 ON c1.country_name = c3.country_name AND c1.year = c3.year
LEFT JOIN  `feature_tables.Government_exp_on_edu` c4 ON c1.country_name = c4.country_name AND c1.year = c4.year
LEFT JOIN  `feature_tables.Internet_users` c5 ON c1.country_name = c5.country_name AND c1.year = c5.year
LEFT JOIN  `feature_tables.School_life_expectancy` c6 ON c1.country_name = c6.country_name AND c1.year = c6.year
LEFT JOIN  `feature_tables.gross_enrollment_rate` c7 ON c1.country_name = c7.country_name AND c1.year = c7.year
LEFT JOIN  `feature_tables.tertiary_proportion` c8 ON c1.country_name = c8.country_name AND c1.year = c8.year
LEFT JOIN  `feature_tables.tertiary_female_to_male_ratio` c9 ON c1.country_name = c9.country_name AND c1.year = c9.year
WHERE MOD(c1.year, 10) = 8
LIMIT 10

label  primary_teacher_percent  primary_female_male_ratio  \
0      0                 0.009401                       0.00   
1      0                 0.001795                       0.23   
2      0                 0.006252                       0.88   
3      0                 0.004548                       0.63   
4      1                 0.008553                       0.59   
5      0                 0.005816                       0.00   
6      0                 0.002870                       0.22   
7      0                 0.000768                       0.33   
8      0                 0.006273                       0.43   
9      0                 0.004790                       0.00   

   popultion_dependency_ratio  Gov_Expenditure_Edu  Internet_user_percent  \
0                    0.714793              0.00000                    0.0   
1                    0.956297              0.00000                    0.0   
2                    0.563615              3.78283                    0.0   
3                    0.481968              4.98988                    0.0   
4                    0.540293              2.77697                    0.0   
5                    0.726833              1.95815                    0.0   
6                    0.966974              0.00000                    0.0   
7                    1.006901              0.00000                    0.0   
8                    1.042148              0.00000                    0.0   
9                    0.718845              0.00000                    0.0   

   school_life_expectancy  gross_enrollment_rate  tertiary_teacher_percent  \
0                11.47051              73.526367                  0.000000   
1                 3.77822              24.667999                  0.000000   
2                12.32693              69.941917                  0.000000   
3                13.18628              78.719528                  0.000000   
4                 0.00000               0.000000                  0.000000   
5                 8.93479              63.034618                  0.000195   
6                 8.15274              50.997921                  0.000087   
7                 1.38054               9.276820                  0.000020   
8                 8.92239              57.417969                  0.000294   
9                 8.56194               0.000000                  0.000873   

   tertiary_female_male_ratio  
0                        0.00  
1                        0.00  
2                        0.00  
3                        0.00  
4                        0.00  
5                        0.27  
6                        0.08  
7                        0.16  
8                        0.20  
9                        0.31

##3.3 Create Model and Train Model
- The model we want to use is the *binary logistic regression model * because this is a classification task: we want to determine the development level of an area with its educatinal features. Each (country, year) is an instance, but we do not include the country name nor year in the features. 
- We want to use this model to train and predict whether a country is a developed one or not(a developed country is defined as GDP oper capita(current US\\$ ) is over $12,000)
- **Data Splitting**: The dataset spans from 1970 to 2016, a total of 47 years. We decide to have around 80% for training, 10% for evaluation, and 10% for test. The way we split the data is to calculate (year mod 10) and choose 0-7 for training, 8 for evaluation and 9 for test.

In [0]:
%%bigquery --project $project_id

# YOUR QUERY HERE

CREATE OR REPLACE MODEL `edu_dataset.model_v1` 
OPTIONS (model_type='logistic_reg') AS
SELECT
  IF(c1.GDP < 12000 , 0, 1) AS label,
  IFNULL(c1.percent,0) AS primary_teacher_percent,
  IFNULL(c2.female_ratio, 0) AS primary_female_male_ratio,
  IFNULL(c3.popultion_dependency_ratio, 0) AS popultion_dependency_ratio,
  IFNULL(c4.Gov_Exp_Edu, 0) AS Gov_Expenditure_Edu,
  IFNULL(c5.Int_user, 0) AS Internet_user_percent,
  IFNULL(c6.expectancy, 0) AS school_life_expectancy,
  IFNULL(c7.GER, 0) AS gross_enrollment_rate,
  IFNULL(c8.percent,0) AS tertiary_teacher_percent,
  IFNULL(c9.female_ratio, 0) AS tertiary_female_male_ratio
FROM `feature_tables.Preprimary_and_primary_proportion` c1 
LEFT JOIN  `feature_tables.Preprimary_and_primary_female_to_male_ratio` c2 ON c1.country_name = c2.country_name AND c1.year = c2.year
LEFT JOIN  `feature_tables.popultion_dependency_ratio` c3 ON c1.country_name = c3.country_name AND c1.year = c3.year
LEFT JOIN  `feature_tables.Government_exp_on_edu` c4 ON c1.country_name = c4.country_name AND c1.year = c4.year
LEFT JOIN  `feature_tables.Internet_users` c5 ON c1.country_name = c5.country_name AND c1.year = c5.year
LEFT JOIN  `feature_tables.School_life_expectancy` c6 ON c1.country_name = c6.country_name AND c1.year = c6.year
LEFT JOIN  `feature_tables.gross_enrollment_rate` c7 ON c1.country_name = c7.country_name AND c1.year = c7.year
LEFT JOIN  `feature_tables.tertiary_proportion` c8 ON c1.country_name = c8.country_name AND c1.year = c8.year
LEFT JOIN  `feature_tables.tertiary_female_to_male_ratio` c9 ON c1.country_name = c9.country_name AND c1.year = c9.year
WHERE MOD(c1.year, 10) < 8

##3.4 Evaluate the Model

In [0]:
%%bigquery --project $project_id

SELECT
  *
FROM
  ML.EVALUATE(MODEL `edu_dataset.model_v1`,(
SELECT
  IF(c1.GDP < 12000 , 0, 1) AS label,
  IFNULL(c1.percent,0) AS primary_teacher_percent,
  IFNULL(c2.female_ratio, 0) AS primary_female_male_ratio,
  IFNULL(c3.popultion_dependency_ratio, 0) AS popultion_dependency_ratio,
  IFNULL(c4.Gov_Exp_Edu, 0) AS Gov_Expenditure_Edu,
  IFNULL(c5.Int_user, 0) AS Internet_user_percent,
  IFNULL(c6.expectancy, 0) AS school_life_expectancy,
  IFNULL(c7.GER, 0) AS gross_enrollment_rate,
  IFNULL(c8.percent,0) AS tertiary_teacher_percent,
  IFNULL(c9.female_ratio, 0) AS tertiary_female_male_ratio
FROM `feature_tables.Preprimary_and_primary_proportion` c1 
LEFT JOIN  `feature_tables.Preprimary_and_primary_female_to_male_ratio` c2 ON c1.country_name = c2.country_name AND c1.year = c2.year
LEFT JOIN  `feature_tables.popultion_dependency_ratio` c3 ON c1.country_name = c3.country_name AND c1.year = c3.year
LEFT JOIN  `feature_tables.Government_exp_on_edu` c4 ON c1.country_name = c4.country_name AND c1.year = c4.year
LEFT JOIN  `feature_tables.Internet_users` c5 ON c1.country_name = c5.country_name AND c1.year = c5.year
LEFT JOIN  `feature_tables.School_life_expectancy` c6 ON c1.country_name = c6.country_name AND c1.year = c6.year
LEFT JOIN  `feature_tables.gross_enrollment_rate` c7 ON c1.country_name = c7.country_name AND c1.year = c7.year
LEFT JOIN  `feature_tables.tertiary_proportion` c8 ON c1.country_name = c8.country_name AND c1.year = c8.year
LEFT JOIN  `feature_tables.tertiary_female_to_male_ratio` c9 ON c1.country_name = c9.country_name AND c1.year = c9.year
WHERE MOD(c1.year, 10) = 8
))

precision    recall  accuracy  f1_score  log_loss   roc_auc
0   0.797753  0.435583  0.859694  0.563492  0.305534  0.909244

##3.5 Testing the Model

In [0]:
%%bigquery --project $project_id
SELECT
  *
FROM
  ML.EVALUATE(MODEL `edu_dataset.model_v1`,(
SELECT
  IF(c1.GDP < 12000 , 0, 1) AS label,
  IFNULL(c1.percent,0) AS primary_teacher_percent,
  IFNULL(c2.female_ratio, 0) AS primary_female_male_ratio,
  IFNULL(c3.popultion_dependency_ratio, 0) AS popultion_dependency_ratio,
  IFNULL(c4.Gov_Exp_Edu, 0) AS Gov_Expenditure_Edu,
  IFNULL(c5.Int_user, 0) AS Internet_user_percent,
  IFNULL(c6.expectancy, 0) AS school_life_expectancy,
  IFNULL(c7.GER, 0) AS gross_enrollment_rate,
  IFNULL(c8.percent,0) AS tertiary_teacher_percent,
  IFNULL(c9.female_ratio, 0) AS tertiary_female_male_ratio
FROM `feature_tables.Preprimary_and_primary_proportion` c1 
LEFT JOIN  `feature_tables.Preprimary_and_primary_female_to_male_ratio` c2 ON c1.country_name = c2.country_name AND c1.year = c2.year
LEFT JOIN  `feature_tables.popultion_dependency_ratio` c3 ON c1.country_name = c3.country_name AND c1.year = c3.year
LEFT JOIN  `feature_tables.Government_exp_on_edu` c4 ON c1.country_name = c4.country_name AND c1.year = c4.year
LEFT JOIN  `feature_tables.Internet_users` c5 ON c1.country_name = c5.country_name AND c1.year = c5.year
LEFT JOIN  `feature_tables.School_life_expectancy` c6 ON c1.country_name = c6.country_name AND c1.year = c6.year
LEFT JOIN  `feature_tables.gross_enrollment_rate` c7 ON c1.country_name = c7.country_name AND c1.year = c7.year
LEFT JOIN  `feature_tables.tertiary_proportion` c8 ON c1.country_name = c8.country_name AND c1.year = c8.year
LEFT JOIN  `feature_tables.tertiary_female_to_male_ratio` c9 ON c1.country_name = c9.country_name AND c1.year = c9.year
WHERE MOD(c1.year, 10) = 9
))

precision   recall  accuracy  f1_score  log_loss   roc_auc
0   0.722222  0.45614  0.843909   0.55914  0.324058  0.896185

##3.6 Closer look at Predictions on Test Set
- It shows that our predictor does a great job in predicting the development level. 
- It has a high precision, meaning whe it predict 1, it is very probable that the true label is 1. 

In [153]:
%%bigquery --project $project_id

# YOUR QUERY HERE
SELECT 
    predicted_label, label
FROM
  ML.PREDICT(MODEL `edu_dataset.model_v1`, (
SELECT
  IF(c1.GDP < 12000 , 0, 1) AS label,
  IFNULL(c1.percent,0) AS primary_teacher_percent,
  IFNULL(c2.female_ratio, 0) AS primary_female_male_ratio,
  IFNULL(c3.popultion_dependency_ratio, 0) AS popultion_dependency_ratio,
  IFNULL(c4.Gov_Exp_Edu, 0) AS Gov_Expenditure_Edu,
  IFNULL(c5.Int_user, 0) AS Internet_user_percent,
  IFNULL(c6.expectancy, 0) AS school_life_expectancy,
  IFNULL(c7.GER, 0) AS gross_enrollment_rate,
  IFNULL(c8.percent,0) AS tertiary_teacher_percent,
  IFNULL(c9.female_ratio, 0) AS tertiary_female_male_ratio
FROM `feature_tables.Preprimary_and_primary_proportion` c1 
LEFT JOIN  `feature_tables.Preprimary_and_primary_female_to_male_ratio` c2 ON c1.country_name = c2.country_name AND c1.year = c2.year
LEFT JOIN  `feature_tables.popultion_dependency_ratio` c3 ON c1.country_name = c3.country_name AND c1.year = c3.year
LEFT JOIN  `feature_tables.Government_exp_on_edu` c4 ON c1.country_name = c4.country_name AND c1.year = c4.year
LEFT JOIN  `feature_tables.Internet_users` c5 ON c1.country_name = c5.country_name AND c1.year = c5.year
LEFT JOIN  `feature_tables.School_life_expectancy` c6 ON c1.country_name = c6.country_name AND c1.year = c6.year
LEFT JOIN  `feature_tables.gross_enrollment_rate` c7 ON c1.country_name = c7.country_name AND c1.year = c7.year
LEFT JOIN  `feature_tables.tertiary_proportion` c8 ON c1.country_name = c8.country_name AND c1.year = c8.year
LEFT JOIN  `feature_tables.tertiary_female_to_male_ratio` c9 ON c1.country_name = c9.country_name AND c1.year = c9.year
WHERE MOD(c1.year, 10) = 9
  ))

predicted_label  label
0                  0      0
1                  0      0
2                  0      0
3                  0      0
4                  0      0
5                  0      0
6                  0      0
7                  0      0
8                  0      0
9                  0      0
10                 0      0
11                 0      0
12                 0      0
13                 0      0
14                 0      0
15                 0      0
16                 0      0
17                 0      0
18                 0      0
19                 0      0
20                 0      0
21                 0      0
22                 0      0
23                 0      0
24                 0      0
25                 0      0
26                 0      0
27                 0      0
28                 0      0
29                 0      0
..               ...    ...
758                1      1
759                1      1
760                1      1
761                1      1
762                1      1
763                1      1
764                1      1
765                1      1
766                1      1
767                1      1
768                1      1
769                1      1
770                1      1
771                1      1
772                1      1
773                1      1
774                1      1
775                1      1
776                1      1
777                1      1
778                1      1
779                1      1
780                1      1
781                1      1
782                1      1
783                1      1
784                1      1
785                1      1
786                1      1
787                1      1

[788 rows x 2 columns]

##3.7 Performance Comments

### How well does our model do? 
- Generally speaking, our model does a decent job in predicting the label (development level). We have used precision, recall, f1, accuracy, log loss and roc_auc to measure the performance of the model. 
- By tuning our model against the evaluation set, our model achieve a good precision of 79.22% and lower precision on test set 72.22%. The accuracy is also great, 85.97% on the evaluation set and 84.29% on the test set. This is reasonable because our model overfitted with the evaluation set. It is also common in machine learning tasks. O
- Our model is not so good in terms of recall, meaning that it is not able to catch all the 1s. In other words, it has many false negatives. The recall as a result causes the F1 score to be low as well because F1 is derived from precision and recall. 
- **Accuracy is the most suitable metrics for our task** because we want our model to both do well in predicting true and false labels. Precision, Recall, and F1 are all biased towards the true label. By following accuracy, our model is doing very well (> 85%).

### Understanding the meanings of metrics
Accoding to the results on the evaluation set, we will get the following conclusions:
- Precision: 0.797753
 - A metric for classification models. Precision identifies the frequency with which a model was correct when predicting the positive class. 
 - So we are confident to say when making pridiction on developed prediction (GDP per capita over 12,000$) , 79.77% of which will be correct. 
- Recall: 0.435583
 - A metric for classification models that answers the following question: Out of all the possible positive labels, how many did the model correctly identify?
 - That is to say, 43.55% of positive label are correctly identified.    
- Accuracy: 0.859694
  - Accuracy is the fraction of predictions that a classification model got right.
  - The overall fraction of predictions that are right are 85.87%. 
- f1_score: 0.563492
  - A measure of the accuracy of the model. The f1 score is the harmonic average of the precision and recall. An f1 score's best value is 1. The worst value is 0. 
- log_loss: 0.305534
   - The loss function used in a logistic regression. This is the measure of how far the model's predictions are from the correct labels.
- roc_auc: 0.909244
  - The area under the ROC curve. This is the probability that a classifier is more confident that a randomly chosen positive example is actually positive than that a randomly chosen negative example is positive.
  - So the probability that a classifier is is more confident  that a classifier is more confident that a randomly chosen developed country is actually a developing one than that a randomly chosen developing country is a developed one is 90.92%. 

#4. Conclusion

##4.1 What I have learned?
- We chosen 9 features out of 15 educational features we explored from the dataset. Those educational features all show some correlations with GDP per Captia, and the 9 picked ones are strongly correlated with GDP per Captia, meaning they are important to the task of predicting the economic development level of a country. 
- Thus, It is rational to use this model to predict the economic development level using given features value. 
- The performance of our model also proves that **the education level and the development level of a country are closely related and we can predict development level from education level**. 


##4.2 What conclusions have you made or been unable to make about your dataset and why? 

### Understand the difference in performance on test set and evaluation set
- By tuning our model against the evaluation set, our model achieve a good precision of 79.22% and lower precision on test set 72.22%. The accuracy is also great, 85.97% on the evaluation set and 84.29% on the test set. This is reasonable because our model **overfitted** with the evaluation set. It is also common in machine learning tasks.

### Review of the Dataset
- the dataset has a huge range of data; however, each survery is conducted in different range of countries and years. Therefore, it results in many NULL values when we join the tables together. 
- Also, this dataset is kind of small, ~600MB. If the dataset is bigger, the logistics regression model should do better because there will be less overfitting. 


### Is 10,000 dollars GDP per Captia in 1970 considered "developing" or "developed"?
- By our standard, 10000 dollars should be labeled as "developing". 
- However, we used GDP per Captia only to approximate the development level of a country. However, this is not accurate because GDP inflates over years and we do not take inflation into account. 10000 dollars in 1970 probably is much more than 12000 in today's standard. 
- If the data has a better measurement of development level, we can use that to label data as developed or developing, which is more accurate. This also explains why our model makes some mistakes. 
- If we can improve the way of labeling the development level, the model is expected to perform better. 
- Thefore, the level of correlation between education and GDP per Captia we concluded is a little questionable unless we fixed the problem of labeling. 


##4.3 What is obvious, and what did you not expect to see?

- Initially, we only pick the first two of the four to avoid using similar features since using similar features will intervene the classification peformance of the model:
  - proportion of preprimary and primary teachers in the whole population
  - female-to-male ratio of preprimary and primary teachers
  - female-to-male ratio of tertiary teachers
  - proportion of tertiary teachers in the whole population
- However, after trials, we find out that by including all the four features, the model performs better by 2% on the evaluation set. Therefore, we include all the four features in our final version. This means that tertiary education should be distinguished from pre-primary and primary education, which is true in many countires. The latter is somehow required in most countries, but the former is optional and more advanced. 
- There are many obvious findings, I will only list a few of them:
  - the higher the proportion of teacher in the population, the more likely the area/country is developed
  - the more expenditure the government spends on education, the more developed the country is likely to be
  - the longer schools attain students (school life expectancy and gross enrollment rate), the more likely the country/area is developed
  - developed countries tend to use more technologies (internet and computer) in education

##4.4  If you had more time, what other data exploration would you pursue?
- Education is only one dimension. We can include features from more fields to predict the economic development level of a country. 
- The topic in this project is to see whether education can be used ot imply whether a counrty is wealthy or not, and the answer is yes. However, there are definitely other data that can be used to predict or reflect the situaton of a country. For example, something involving military force, culture exporting, technology inovation may all have potential correlation with economic development. If we have more time, we would like to investigate such coorelation. Furtherly, set all these topics as features by using a index to represent each of them and create a model contributed by all topic mentioned. That would be a muti-dimention model containing education, military, culture, agriculture, etc.   


### GDP or Purchasing Power Parity (PPP)
- In this project, we use GDP per capita as the factor to represent whether a country is a developed one or a developing one. In practice, there are other factors that should be taken into consideration. For example, 1$ in the US can buy much less items tan in Korea, DPR, which would be the same with education. That is too say, at least Real exchange rate will influence the result. Maybe PPP makes more sense in some cases than GDP. 